# Description:

* Quick and dirty creation of a 16S rRNA tree of OTUs

In [1]:
workDir = '/home/bryan/RhizCG/data/MiSeq_amplicon/MergedRuns/fasttree/'
OTUFileDir = '/home/bryan/RhizCG/data/MiSeq_amplicon/MergedRuns/OTU_binning/'
OTUFile = 'otusn.pick.fasta'

seqFile = '/home/bryan/RhizCG/data/MiSeq_amplicon/MergedRuns/QC/finalQC_M.fasta'
nprocs = 20

In [2]:
import os
import numpy as np
from cogent.app.fasttree import build_tree_from_alignment
from cogent import DNA, LoadSeqs
from Bio import Entrez
Entrez.email = "chuck.peperanney@gmail.com"
from IPython.display import display, Image, SVG



In [3]:
%load_ext rpy2.ipython

In [29]:
%%R
library(dplyr)
library(tidyr)
library(ggplot2)

/opt/anaconda/lib/python2.7/site-packages/rpy2/robjects/functions.py:106: UserWarning: 
Attaching package: ‘dplyr’


  res = super(Function, self).__call__(*new_args, **new_kwargs)
/opt/anaconda/lib/python2.7/site-packages/rpy2/robjects/functions.py:106: UserWarning: The following objects are masked from ‘package:stats’:

    filter, lag


  res = super(Function, self).__call__(*new_args, **new_kwargs)
/opt/anaconda/lib/python2.7/site-packages/rpy2/robjects/functions.py:106: UserWarning: The following objects are masked from ‘package:base’:

    intersect, setdiff, setequal, union


  res = super(Function, self).__call__(*new_args, **new_kwargs)


In [4]:
if not os.path.isdir(workDir):
    os.mkdir(workDir)

In [5]:
%cd $workDir

/home/bryan/RhizCG/data/MiSeq_amplicon/MergedRuns/fasttree


In [6]:
!cd $workDir; ln -f -s $OTUFileDir$OTUFile

In [7]:
!cd $workDir; head $OTUFile

>OTU.3
TACGTAGGGCGCAAGCGTTGTCCGGAATTATTGGGCGTAAAGAGCTCGTAGGCGGCTTGTCACGTCGGGTGTGAAAGCTCGGGGCTTAACCCCGGGTCTGCATTCGATACGGGCTGGCTGGAGTGTGGTAGGGGAGATCGGAATTCCTGGTGTAGCGGTGAAATGCGCAGATATCAGGAGGAACACCGGTGGCGAAGGCGGATCTCTGGGCCATTACTGACGCTGAGGAGCGAAAGCGTGGGGAGCGAACAGG
>OTU.4
TACGTAGGGTGCAAGCGTTAATCGGAATTACTGGGCGTAAAGCGTGCGCAGGCGGTTTCGTAAGTCTGTCGTGAAATCCCCGGGCTTAACCTGGGAATGGCGATGGAGACTGCGAGGCTAGAGTTTGGCAGAGGGGGGTAGAATTCCACGTGTAGCAGTGAAATGCGTAGAGATGTGGAGGAACACCGATGGCGAAGGCAGCCCCCTGGGTCAAAACTGACGCTCATGCACGAAAGCGTGGGGAGCAAACAGG
>OTU.5
TACGGAGGGTGCAAGCGTTAATCGGAATTACTGGGCGTAAAGCGCACGCAGGCGGTCTGTCAAGTCGGATGTGAAATCCCCGGGCTCAACCTGGGAACTGCATTCGAAACTGGCAGGCTAGAGTCTTGTAGAGGGGGGTAGAATTCCAGGTGTAGCGGTGAAATGCGTAGAGATCTGGAGGAATACCGGTGGCGAAGGCGGCCCCCTGGACAAAGACTGACGCTCAGGTGCGAAAGCGTGGGGAGCAAACAGG
>OTU.6
CACGTAGGGGACGAGCGTTGTCCGGATTCATTGGGCGTAAAGCGCGCGTAGGCGGCTCGGAAAGTCGGGCGTGAAATGCCGGGGCTCAACCCCGGGACTGCGTCCGATACTTCCGAGCTGGAGGTAGGTAGGGGAGATCGGAATTCCTGGTGTAGCGGTGAAATGCGCAGATATCAGGAGGAACACCGGTGGCGAAGGCGGATCTCTGGG

In [8]:
!printf "Number of OTUs in fasta: "
!cd $workDir; grep -c ">" $OTUFile

Number of OTUs in fasta: 11246


## Using SSU-Align to align seqs and masking based on alignment posterior probabilities.

In [9]:
!cd $workDir; ssu-prep -f -x -b 50 --rfonly --dna $OTUFile ssu_aln 20 

# ssu-prep :: prepare SSU rRNA sequences for parallel ssu-align jobs
# SSU-ALIGN 0.1 (June 2010)
# Copyright (C) 2010 HHMI Janelia Farm Research Campus
# Freely distributed under the GNU General Public License (GPLv3)
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# command: ssu-prep -x -f -b 50 --dna --rfonly otusn.pick.fasta ssu_aln 20
# date:    Wed Apr 27 10:14:03 2016
#
# Validating input sequence file ... done.
#
# Preparing 20 ssu-align jobs ...
# Partitioning seqs with goal of equalizing total number of nucleotides per job ...
#
# output file name      description                                           
# --------------------  ------------------------------------------------------
  ssu_aln/otusn.pick.fasta.1  partition  1 FASTA sequence file (563 seqs; 142512 nt)
  ssu_aln/otusn.pick.fasta.2  partition  2 FASTA sequence file (563 seqs; 142561 nt)
  ssu_aln/otusn.pick.fasta.3  partition  3 FASTA sequence file (563 seqs; 142552 nt)
  ssu_aln/otusn.p

In [10]:
!cd $workDir; ./ssu_aln.ssu-align.sh

# Executing: ssu-align -b 50 --dna --rfonly ssu_aln/otusn.pick.fasta.1 ssu_aln/ssu_aln.1 > /dev/null &
# Executing: ssu-align -b 50 --dna --rfonly ssu_aln/otusn.pick.fasta.2 ssu_aln/ssu_aln.2 > /dev/null &
# Executing: ssu-align -b 50 --dna --rfonly ssu_aln/otusn.pick.fasta.3 ssu_aln/ssu_aln.3 > /dev/null &
# Executing: ssu-align -b 50 --dna --rfonly ssu_aln/otusn.pick.fasta.4 ssu_aln/ssu_aln.4 > /dev/null &
# Executing: ssu-align -b 50 --dna --rfonly ssu_aln/otusn.pick.fasta.5 ssu_aln/ssu_aln.5 > /dev/null &
# Executing: ssu-align -b 50 --dna --rfonly ssu_aln/otusn.pick.fasta.6 ssu_aln/ssu_aln.6 > /dev/null &
# Executing: ssu-align -b 50 --dna --rfonly ssu_aln/otusn.pick.fasta.7 ssu_aln/ssu_aln.7 > /dev/null &
# Executing: ssu-align -b 50 --dna --rfonly ssu_aln/otusn.pick.fasta.8 ssu_aln/ssu_aln.8 > /dev/null &
# Executing: ssu-align -b 50 --dna --rfonly ssu_aln/otusn.pick.fasta.9 ssu_aln/ssu_aln.9 > /dev/null &
# Executing: ssu-align -b 50 --dna --rfonly ssu_aln/otusn.pick.fasta.10 s

In [11]:
!cd $workDir; ssu-mask --dna --afa ssu_aln

# ssu-mask :: mask SSU rRNA alignments
# SSU-ALIGN 0.1 (June 2010)
# Copyright (C) 2010 HHMI Janelia Farm Research Campus
# Freely distributed under the GNU General Public License (GPLv3)
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# command: ssu-mask --afa --dna ssu_aln
# date:    Wed Apr 27 10:15:49 2016
#
# Masking alignments based on posterior probabilities...
#
#                                                     mask    
#                                                 ------------
# file name                  in/out  type  #cols  incl.  excl.
# -------------------------  ------  ----  -----  -----  -----
  ssu_aln.bacteria.stk        input   aln   1582      -      -
  ssu_aln.bacteria.mask      output  mask   1582    249   1333
  ssu_aln.bacteria.mask.pdf  output   pdf   1582    249   1333
  ssu_aln.bacteria.mask.afa  output   aln    249      -      -
#
# All attempts to draw structure diagrams of masks were successful.
#
# List of executed comman

In [12]:
!cd $workDir; seq_tools fasta_unwrap ssu_aln/ssu_aln.bacteria.mask.afa | head

>OTU.3
TACGTAGGGCGCAAGCGTTGTCCGGAATTATTGGGCGTAAAGAGCTCGTAGGCGGCTTGTCACGTCGGGTGTGAAAGCTCGGGGCTTAACCCCGGGTCCATTCGATACGGGCTGGCTGGAGTGTGGTAGGGGAGATCGGAATTCCTGGTGTAGCGGTGAAATGCGCAGATATCAGGAGGAACACCGGTGGCGAAGGCGGATCTCTGGGCCAACTGACGCTGAGGAGCGAAAGCGTGGGGAGCGAACAGG
>OTU.4
TACGTAGGGTGCAAGCGTTAATCGGAATTACTGGGCGTAAAGCGTGCGCAGGCGGTTTCGTAAGTCTGTCGTGAAATCCCCGGGCTTAACCTGGGAATCGATGGAGACTGCGAGGCTAGAGTTTGGCAGAGGGGGGTAGAATTCCACGTGTAGCAGTGAAATGCGTAGAGATGTGGAGGAACACCGATGGCGAAGGCAGCCCCCTGGGTCAACTGACGCTCATGCACGAAAGCGTGGGGAGCAAACAGG
>OTU.5
TACGGAGGGTGCAAGCGTTAATCGGAATTACTGGGCGTAAAGCGCACGCAGGCGGTCTGTCAAGTCGGATGTGAAATCCCCGGGCTCAACCTGGGAACCATTCGAAACTGGCAGGCTAGAGTCTTGTAGAGGGGGGTAGAATTCCAGGTGTAGCGGTGAAATGCGTAGAGATCTGGAGGAATACCGGTGGCGAAGGCGGCCCCCTGGACAAACTGACGCTCAGGTGCGAAAGCGTGGGGAGCAAACAGG
>OTU.6
-ACGTAGGGGACGAGCGTTGTCCGGATTCATTGGGCGTAAAGCGCGCGTAGGCGGCTCGGAAAGTCGGGCGTGAAATGCCGGGGCTCAACCCCGGGACCGTCCGATACTTCCGAGCTGGAGGTAGGTAGGGGAGATCGGAATTCCTGGTGTAGCGGTGAAATGCGCAGATATCAGGAGGAACACCGGTGGCGAAGGCGGATCTCTGGGCCTCCTGACGCTGA

### Using Sulfolobus as the root (acc. X90478).

In [13]:
sso_acc = "X90478"
sso_fa = Entrez.efetch(db="nucleotide", id=sso_acc, rettype="fasta", retmode="text").readlines()

In [14]:
out = open(os.path.join(workDir, 'X90478.fasta'), 'w')
sso_fa_namestrip = sso_fa[1:]
sso_fa_namestrip.insert(0,">%s\n"%sso_acc)
out.writelines(sso_fa_namestrip)
out.close()

In [15]:
!cd $workDir; head -n 4 X90478.fasta

>X90478
TCCTGCCGGTCCCGACCGCTATCGGGGTGGGGCTAAGCCATGGGAGTCGTACGCTCCCGGGCAAGGGAGC
GTGGCGGACGGCTGAGTAACACGTGGCTAACCTACCCTGAGGAGGGAGATAACCCCGGGAAACTGGGGAT
AATCTCCCATAGGCGAGGAGTCCTGGAACGGTTCCTCGCTGAAAGGCTCATGGGCTATTCCCCGCTCATG


### Align the outgroup to the same cm (use the same mask that was established earlier).

In [16]:
!cd $workDir; ssu-align -f -n bacteria --dna --rfonly X90478.fasta sso_aln

# ssu-align :: align SSU rRNA sequences
# SSU-ALIGN 0.1 (June 2010)
# Copyright (C) 2010 HHMI Janelia Farm Research Campus
# Freely distributed under the GNU General Public License (GPLv3)
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# command: ssu-align -f -n bacteria --dna --rfonly X90478.fasta sso_aln
# date:    Wed Apr 27 10:16:21 2016
#
# Validating input sequence file ... done.
#
# Stage 1: Determining SSU start/end positions and best-matching models...
#
# output file name          description                                
# ------------------------  -------------------------------------------
  sso_aln.tab               locations/scores of hits defined by HMM(s)
  sso_aln.bacteria.hitlist  list of sequences to align with bacteria CM
  sso_aln.bacteria.fa             1 sequence  to align with bacteria CM
#
# Stage 2: Aligning each sequence to its best-matching model...
#
# output file name          description
# ------------------------  ----------

In [17]:
!cd $workDir; ssu-mask -s ssu_aln/ssu_aln.bacteria.mask --dna --afa sso_aln/

# ssu-mask :: mask SSU rRNA alignments
# SSU-ALIGN 0.1 (June 2010)
# Copyright (C) 2010 HHMI Janelia Farm Research Campus
# Freely distributed under the GNU General Public License (GPLv3)
# - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - - -
# command: ssu-mask -s ssu_aln/ssu_aln.bacteria.mask --afa --dna sso_aln/
# date:    Wed Apr 27 10:16:30 2016
#
# Masking alignments using pre-existing masks...
#
#                                                     mask    
#                                                 ------------
# file name                  in/out  type  #cols  incl.  excl.
# -------------------------  ------  ----  -----  -----  -----
  sso_aln.bacteria.stk        input   aln   1582      -      -
  ssu_aln.bacteria.mask       input  mask   1582    249   1333
  sso_aln.bacteria.mask.pdf  output   pdf   1582    249   1333
  sso_aln.bacteria.mask.afa  output   aln    249      -      -
#
# All attempts to draw structure diagrams of masks were successful.
#

In [18]:
!cd $workDir; /home/bryan/seq_tools/seq_tools fasta_unwrap sso_aln/sso_aln.bacteria.mask.afa | head

>X90478
TACCAGCCCCGCGAG---TGGTCGGGATTACTGGGCCTAAAGCGCCCGTAGCCGGCCCGACAAGTCACTCCTTAAAGACCCCGGCTCAACCGGGGGAAGGGGTGATACTGTCGGGCTAGGGGGCGGGAGAGGCCAGCGGTACTCCCGGAGTAGGGGCGAAATCCTCAGATCTCGGGAGGACCACCAGTGGCGAAAGCGGCTGGCTAGAACGCCCGACGGTGAGGGGCGAAAGCCGGGGCAGCAAAAGGG

In [19]:
!cd $workDir; cat sso_aln/sso_aln.bacteria.mask.afa ssu_aln/ssu_aln.bacteria.mask.afa > aln_for_tree.fasta

In [20]:
!cd $workDir; /home/bryan/seq_tools/seq_tools fasta_unwrap aln_for_tree.fasta | head

>X90478
TACCAGCCCCGCGAG---TGGTCGGGATTACTGGGCCTAAAGCGCCCGTAGCCGGCCCGACAAGTCACTCCTTAAAGACCCCGGCTCAACCGGGGGAAGGGGTGATACTGTCGGGCTAGGGGGCGGGAGAGGCCAGCGGTACTCCCGGAGTAGGGGCGAAATCCTCAGATCTCGGGAGGACCACCAGTGGCGAAAGCGGCTGGCTAGAACGCCCGACGGTGAGGGGCGAAAGCCGGGGCAGCAAAAGGG
>OTU.3
TACGTAGGGCGCAAGCGTTGTCCGGAATTATTGGGCGTAAAGAGCTCGTAGGCGGCTTGTCACGTCGGGTGTGAAAGCTCGGGGCTTAACCCCGGGTCCATTCGATACGGGCTGGCTGGAGTGTGGTAGGGGAGATCGGAATTCCTGGTGTAGCGGTGAAATGCGCAGATATCAGGAGGAACACCGGTGGCGAAGGCGGATCTCTGGGCCAACTGACGCTGAGGAGCGAAAGCGTGGGGAGCGAACAGG
>OTU.4
TACGTAGGGTGCAAGCGTTAATCGGAATTACTGGGCGTAAAGCGTGCGCAGGCGGTTTCGTAAGTCTGTCGTGAAATCCCCGGGCTTAACCTGGGAATCGATGGAGACTGCGAGGCTAGAGTTTGGCAGAGGGGGGTAGAATTCCACGTGTAGCAGTGAAATGCGTAGAGATGTGGAGGAACACCGATGGCGAAGGCAGCCCCCTGGGTCAACTGACGCTCATGCACGAAAGCGTGGGGAGCAAACAGG
>OTU.5
TACGGAGGGTGCAAGCGTTAATCGGAATTACTGGGCGTAAAGCGCACGCAGGCGGTCTGTCAAGTCGGATGTGAAATCCCCGGGCTCAACCTGGGAACCATTCGAAACTGGCAGGCTAGAGTCTTGTAGAGGGGGGTAGAATTCCAGGTGTAGCGGTGAAATGCGTAGAGATCTGGAGGAATACCGGTGGCGAAGGCGGCCCCCTGGACAAACTGACGCTC

## Inferring and rooting the tree

In [21]:
aln = LoadSeqs(os.path.join(workDir, 'aln_for_tree.fasta'), moltype=DNA)
t_unroot = build_tree_from_alignment(aln, moltype=DNA)

In [22]:
t_rooted = t_unroot.rootedWithTip(sso_acc)

In [23]:
t_rooted.writeToFile(os.path.join(workDir, 'otusn_pick.tree'))

In [24]:
# ladderize tree
!cd $workDir; /home/bryan/bin/tree_edit/tree_edit ladderize -t otusn_pick.tree

## viewing tree

In [25]:
!cd $workDir; \
    nw_display -i 'visibility:hidden' -l 'visibility:hidden' -b 'opacity:0' \
    -S -s -r otusn_pick_lad.nwk > otusn_pick_lad_nwk.svg

In [26]:
treePic = os.path.join(workDir, 'otusn_pick_lad_nwk.svg')

SVG(filename=treePic)

In [ ]:
!pwd

## tree summary

In [27]:
!cd $workDir
!printf "Number of tree tips: "
!nw_labels -I otusn_pick_lad.nwk | wc -l

Number of tree tips: 11247


# Making 'bootstrap' trees

* FastTree doesn't write out each bootstrap tree, just bootstrap values on the final tree
* Need the bootstrap trees for concenTRAIT 
* Making the bootstrap trees 'manually' by bootstrapping the alignment and writting the trees

In [42]:
alnFile = os.path.join(workDir, 'aln_for_tree.fasta')
bootFile = os.path.splitext(alnFile)[0] + '_boot.nwk'
!/home/bryan/tree_edit/bin/FastTree_bootTrees.py -p 20 $alnFile > $bootFile

Inferring bootstrap tree: 1
Inferring bootstrap tree: 3
Inferring bootstrap tree: 5
Inferring bootstrap tree: 7
Inferring bootstrap tree: 9
Inferring bootstrap tree: 11
Inferring bootstrap tree: 13
Inferring bootstrap tree: 15
Inferring bootstrap tree: 17
Inferring bootstrap tree: 19
Inferring bootstrap tree: 21
Inferring bootstrap tree: 23
Inferring bootstrap tree: 25
Inferring bootstrap tree: 27
Inferring bootstrap tree: 29
Inferring bootstrap tree: 31
Inferring bootstrap tree: 33
Inferring bootstrap tree: 35
Inferring bootstrap tree: 37
Inferring bootstrap tree: 39
Inferring bootstrap tree: 26
Inferring bootstrap tree: 34
Inferring bootstrap tree: 24
Inferring bootstrap tree: 30
Inferring bootstrap tree: 8
Inferring bootstrap tree: 32
Inferring bootstrap tree: 12
Inferring bootstrap tree: 10
Inferring bootstrap tree: 2
Inferring bootstrap tree: 14
Inferring bootstrap tree: 38
Inferring bootstrap tree: 36
Inferring bootstrap tree: 40
Inferring bootstrap tree: 28
Inferring bootstrap t

In [43]:
!wc -l $bootFile

100 /home/bryan/RhizCG/data/MiSeq_amplicon/MergedRuns/fasttree/aln_for_tree_boot.nwk
